### Design a Singapore traffic report system.

The system will collect data from the Singapore LTA data link as follow

Read the road incidents from API
http://datamall2.mytransport.sg/ltaodataservice/TrafficIncidents
Read the road traffic bands from API

http://datamall2.mytransport.sg/ltaodataservice/TrafficSpeedBandsv2

Program collect the data from the mentioned API above and display on a visualization graph.
The visualization graph should display the Singapore map with different markers to indicate the traffic incident and traffic bands at each location.


1. Python program request the traffic incident URL and return the JSON data
2. Extract and format the traffic incident data require for display in Singapore map
3. Python program request the traffic band URL and return the JSON data
4. Extract and format the traffic band data require for display in Singapore
map
5. Add the data into the display map with different markers to represent the traffic incident and traffic bands
6. When clicking on the marker on the display map it should show the information of either traffic incident or traffic bands

In [1]:
import folium
import requests 
import json


headers = { 'AccountKey' : "InputOwnAPIKeyHere',
'accept' : 'application/json'} #this is by default

#using API request to retrieve TrafficIncidents.

r=requests.get("http://datamall2.mytransport.sg/ltaodataservice/TrafficIncidents", headers=headers)

print(type(r))
dataTrafficIncidents = r.json() 
print(type(dataTrafficIncidents)) 
dataTrafficIncidents

<class 'requests.models.Response'>
<class 'dict'>


{'odata.metadata': 'http://datamall2.mytransport.sg/ltaodataservice/$metadata#IncidentSet',
 'value': [{'Type': 'Vehicle breakdown',
   'Latitude': 1.3206658696966906,
   'Longitude': 103.88101949346894,
   'Message': '(29/6)12:09 Vehicle breakdown on PIE (towards Changi Airport) after Kallang Way.'},
  {'Type': 'Vehicle breakdown',
   'Latitude': 1.2836434304303723,
   'Longitude': 103.80932398741717,
   'Message': '(29/6)12:05 Vehicle breakdown on AYE (towards MCE) after Alexandra.'},
  {'Type': 'Roadwork',
   'Latitude': 1.283733937716833,
   'Longitude': 103.8073289599577,
   'Message': '(29/6)11:56 Roadworks on AYE (towards MCE) after Alexandra. Avoid lane 3.'},
  {'Type': 'Roadwork',
   'Latitude': 1.35260489482729,
   'Longitude': 103.78901425701761,
   'Message': '(29/6)11:41 Roadworks on BKE (towards Woodlands) after PIE Entrance.'},
  {'Type': 'Obstacle',
   'Latitude': 1.2852079828716434,
   'Longitude': 103.83770155767992,
   'Message': '(29/6)11:39 Obstacle in CTE Tunnel (

In [2]:
# Exract the date, time and message from 'Message'
# Create a simple HTML to display the information

import re
def htmlText(text, incidenttype):
    left_col_colour = "#cd4746"
    right_col_colour = "#f2a652"
    
    datetext=re.compile(r"\((\d+/\d+)\)")
    timetext=re.compile(r"(\d+:\d+)")
    messagetext=re.compile(r" (.*)")
    datetext=datetext.match(text).group()
    timetext=timetext.search(text).group() 
    messagetext=messagetext.search(text).group()
    #print(messagetext)
    #print(incidenttype)
    
    
    html = """<!DOCTYPE html>
<html>

<head>
<h6 style="margin-bottom:0"; width="200px"> Date : {}. Type: {}</h6>""".format(datetext,incidenttype) + """

</head>
    <table style="height: 126px; width: 200px;">
<tbody>
<tr>
<td style="width:60px;background-color: """+ left_col_colour +""";"><span style="color: #ffffff;">Time</span></td>
<td style="width: 140px;background-color: """+ right_col_colour +""";">  {}</td>""".format(timetext) + """
</tr>
<tr>
<td style="width:60px;background-color: """+ left_col_colour +""";"><span style="color: #ffffff;">Message</span></td>
<td style="width: 140px;background-color: """+ right_col_colour +""";"> {}</td>""".format(messagetext) + """
</tr>
</tbody>
</table>
</html>
"""
    return html

In [3]:
from folium.plugins import MarkerCluster


sg_map=folium.Map(location=[1.28,103.85],zoom_start=11)

#at the time of this assignment, the number of traffic incidents is low.
#but in anticipation that there may be more future incidents, MarkerCluster class is used to group the icons 
#so that the map is less cluttered. 

marker_cluster=MarkerCluster().add_to(sg_map)

for i in dataTrafficIncidents['value']:
    #display(i['Type'], i['Latitude'], i['Longitude'],i['Message'])
    #display(i['Message'])
    
    text=''.join(i['Message'])
    htmltxt=htmlText(text, i['Type'])

    #print(text)
    
    folium.Marker(
        location=[i['Latitude'], i['Longitude']],
        popup=folium.Popup(html=htmltxt,parse_html=False,max_width='100%'), icon=folium.Icon(color='red',icon='info-sign')
    ).add_to(marker_cluster)

sg_map

In [4]:
#Using API requests to get TrafficSpeedBands
#It is noticed that the number of rows of data for TrafficSpeedBands is about 60000.
#Although it is possible to extract all the rows, the rendering of the map takes a long time.
#In the interest of the time and resources,first 1000 rows will be extracted for illustration. 

url="http://datamall2.mytransport.sg/ltaodataservice/TrafficSpeedBandsv2"

r2=requests.get("http://datamall2.mytransport.sg/ltaodataservice/TrafficSpeedBandsv2", headers=headers)

dataTrafficSpeedBands = r2.json() 
#print(type(dataTrafficIncidents)) 
#dataTrafficSpeedBands

counter=500
r3=requests.get(url+"?$skip="+str(counter),headers=headers)
temp=r3.json()

dataTrafficSpeedBands['value']=dataTrafficSpeedBands['value']+(temp['value'])
display(len(dataTrafficSpeedBands['value']),dataTrafficSpeedBands)


1000

{'odata.metadata': 'http://datamall2.mytransport.sg/ltaodataservice/$metadata#TrafficSpeedBandsv2',
 'value': [{'LinkID': '103000000',
   'RoadName': 'KENT ROAD',
   'RoadCategory': 'E',
   'SpeedBand': 3,
   'MinimumSpeed': '20',
   'MaximumSpeed': '29',
   'Location': '1.3170142376560023 103.85298052044503 1.3166840028663076 103.85259882242372'},
  {'LinkID': '103000010',
   'RoadName': 'BUCKLEY ROAD',
   'RoadCategory': 'E',
   'SpeedBand': 3,
   'MinimumSpeed': '20',
   'MaximumSpeed': '29',
   'Location': '1.3166507852203482 103.84102305136321 1.316912438354752 103.84022564204443'},
  {'LinkID': '103000011',
   'RoadName': 'BUCKLEY ROAD',
   'RoadCategory': 'E',
   'SpeedBand': 4,
   'MinimumSpeed': '30',
   'MaximumSpeed': '39',
   'Location': '1.316912438354752 103.84022564204443 1.3166507852203482 103.84102305136321'},
  {'LinkID': '103000014',
   'RoadName': 'SHREWSBURY ROAD',
   'RoadCategory': 'E',
   'SpeedBand': 4,
   'MinimumSpeed': '30',
   'MaximumSpeed': '39',
   'Loca

In [5]:
#this function is to calculate the distance between the two points represented in 'Location'
#Presenting the distance information to user is useful as it allows the user to estimate
#how long is the distance convered by the speed band. Otherwise, user will have to guess where it ends using
#landmarks. 

import math


def distance(origin, destination):

    lat1, lon1 = origin
    lat2, lon2 = destination
    radius = 6371  # in km. Estimated radius of Earth.

    dlat = math.radians(lat2 - lat1)
    dlon = math.radians(lon2 - lon1)
    a = (math.sin(dlat / 2) * math.sin(dlat / 2) +
         math.cos(math.radians(lat1)) * math.cos(math.radians(lat2)) *
         math.sin(dlon / 2) * math.sin(dlon / 2))
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    d = radius * c

    return round(d*1000,1) #the distance is returned in metres.


In [6]:
#parse the 'Location' string into two list, called origin and destination.
#origin represent the starting location, destination represent the ending location.
#the two information is required to calculate the distance between the two points. 

def convertLocation(locale):


    #print(locale)

    origin=[float(locale[0]),float(locale[1])]
    destination=[float(locale[2]),float(locale[3])]
    
    return origin, destination


In [7]:
#color coding the speed bands.
#Lower speed band means slower speed, and the color is red.
#Higher speed band is represented by green color. 

def speedMarker(text):
    if int(text)<=3:
        return 'red'
    elif int(text)<=5:
        return 'orange'
    elif int(text)>=6:
        return 'green'

In [8]:
#this prepare a html code to present the relevant information in the popup when user click the icon. 

def messageText(roadName,minSpeed,maxSpeed,dist,text):
    left_col_colour = "#2A799C"
    right_col_colour = "#C5DCE7"
    
    messageString=''
    if int(maxSpeed)==999:
        ms='Up To Speed Limit'
    else:
        ms=int(maxSpeed)
    
    html = """<!DOCTYPE html>
<html>

<head>
<h6 style="margin-bottom:0"; width="300px">Road Name :{}</h6>""".format(roadName) + """

</head>
    <table style="height: 126px; width: 300px;">
<tbody>
<tr>
<td style="background-color: """+ left_col_colour +""";"><span style="color: #ffffff;">Min Speed</span></td>
<td style="width: 200px;background-color: """+ right_col_colour +""";">{} km/h</td>""".format(int(minSpeed)) + """
</tr>
<tr>
<td style="background-color: """+ left_col_colour +""";"><span style="color: #ffffff;">Max Speed </span></td>
<td style="width: 200px;background-color: """+ right_col_colour +""";">{} km/h</td>""".format(ms) + """
</tr>
<tr>
<td style="background-color: """+ left_col_colour +""";"><span style="color: #ffffff;">Speed Band Distance</span></td>
<td style="width: 200px;background-color: """+ right_col_colour +""";">{} m</td>""".format(dist) + """
</tr>
<tr>
<td style="background-color: """+ left_col_colour +""";"><span style="color: #ffffff;">Speed Band (1-8)</span></td>
<td style="width: 200px;background-color: """+ right_col_colour +""";">{} </td>""".format(text) + """
</tr>
</tbody>
</table>
</html>
"""
    return html

In [9]:
marker_cluster2=MarkerCluster().add_to(sg_map)


for i in dataTrafficSpeedBands['value']:
   
    
    text=str(i['SpeedBand'])
    iconColor=speedMarker(text)
    
    locale=i['Location'].split()
    origin, destination=convertLocation(locale)
    dist = distance(origin, destination)
    
    roadName= i['RoadName']
    minSpeed=i['MinimumSpeed']
    maxSpeed=i['MaximumSpeed']
    
    message=messageText(roadName,minSpeed,maxSpeed,dist, text)
    
    #PolyLine is used to present the distance between the two points covered by the speed band.
    
    folium.PolyLine(
        locations=[origin, destination],
        #popup="Test", icon=folium.Icon(color='red',icon='info-sign')
        popup=folium.Popup(html=message,parse_html=False,max_width='100%'), color=iconColor, dash_array='6',
        dash_offset=1,
        smooth_factor=10, no_clip=True
        #popup=folium.Popup(r"<b>{}</b>".format(i['Message']),parse_html=True, max_width='100'), icon=folium.Icon(color='red',icon='info-sign')
    ).add_to(sg_map)
    
    #The start and end points of the speed band is represented by circle marker. 
    #Because some start and end points may be represented several times because they share the location,
    #it is neccessary to make the circle less opaque and allow PolyLine above to be visible to 
    #enhance understanding of the information . 
    
    folium.Circle(
        location=[origin[0], origin[1]], radius=8,
        #popup="Test", icon=folium.Icon(color='red',icon='info-sign')
        popup=folium.Popup(html=message,parse_html=False,max_width='100%'), color=iconColor, dash_array='5',
        fill=True, fill_opacity=0.1,fill_color=iconColor
        #popup=folium.Popup(r"<b>{}</b>".format(i['Message']),parse_html=True, max_width='100'), icon=folium.Icon(color='red',icon='info-sign')
    ).add_to(marker_cluster2)
    
    folium.Circle(
        location=[destination[0], destination[1]], radius=8,
        #popup="Test", icon=folium.Icon(color='red',icon='info-sign')
        popup=folium.Popup(html=message,parse_html=False,max_width='100%'), color=iconColor, dash_array='5',
        fill=True,fill_opacity=0.1,fill_color=iconColor
        #popup=folium.Popup(r"<b>{}</b>".format(i['Message']),parse_html=True, max_width='100'), icon=folium.Icon(color='red',icon='info-sign')
    ).add_to(sg_map)
    


sg_map